Данная задача типа "Question-Answering". Для дообучения (fine-tuning) была взята модель BERT, обученная на русских текстах - rubert-tiny2(автор Давид Дале @cointegrated)

Обучение производилось на платформе Google Colab с использованием Hugging face API. 

Загрузка и обработка данных

In [1]:
import json
with open('train.json', 'r') as f:
    data = json.load(f)

In [2]:
def answer_positions(dataset):
  new_dataset = dataset
  for i in range(len(dataset)):
    new_dataset[i]['extracted_part']['text'] = dataset[i]['extracted_part']['text'][0]
    new_dataset[i]['extracted_part']['answer_start'] = dataset[i]['extracted_part']['answer_start'][0]
    new_dataset[i]['extracted_part']['answer_end'] = dataset[i]['extracted_part']['answer_end'][0]
  return new_dataset

In [3]:
def prep_data(dataset):
  ids = []
  questions = []
  contexts = []
  answers = []
  new_dataset = answer_positions(dataset)
  for i in range(len(dataset)):
    ids.append(dataset[i]['id'])
    questions.append(dataset[i]['label'])
    contexts.append(dataset[i]['text'])
    answers.append(new_dataset[i]['extracted_part'])
  return {
      'id': ids,
      'question': questions,
      'context': contexts,
      'answers': answers
  }

In [4]:
dataset = prep_data(data)

In [5]:
import pandas as pd

In [6]:
cols = ['id', 'context','question','answers']

data_df = pd.DataFrame(dataset, columns=cols) 

In [8]:
data_df['question'].unique()

array(['обеспечение исполнения контракта',
       'обеспечение гарантийных обязательств'], dtype=object)

In [9]:
len(data_df[data_df['question']=='обеспечение исполнения контракта'])

988

In [10]:
len(data_df[data_df['question']=='обеспечение гарантийных обязательств'])

811

In [11]:
val_data = data_df[:360].reset_index(drop=True)
train_data = data_df[360:].reset_index(drop=True)

In [13]:
len(train_data[train_data['question']=='обеспечение исполнения контракта'])

634

In [12]:
len(train_data[train_data['question']=='обеспечение гарантийных обязательств'])

805

Токенизация данных

In [9]:
!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 88.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 25.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 108.0 MB/s eta 0:00:00


In [10]:
from transformers import AutoTokenizer

model_checkpoint = 'cointegrated/rubert-tiny2'
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)

Пример работы токенайзера

In [16]:
max_length = 512
stride = 128
inputs = tokenizer(data_df["question"][5], 
                   data_df["context"][5],
                   max_length=max_length,
                   truncation="only_second",
                   stride=stride,
                   return_overflowing_tokens=True,
                   return_offsets_mapping=True,
                   padding='max_length',)

In [17]:
for ids in inputs["input_ids"]:
    print(tokenizer.decode(ids))

[CLS] обеспечение исполнения контракта [SEP] Приложение № 3 ГОСУДАРСТВЕННЫЙ КОНТРАКТ ( ПРОЕКТ ) на приобретение перчаток резиновых хозяйственных для столовой ФКУ УК ГУФСИН России по Красноярскому краю № _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ ( номер государственного контракта ) г. Красноярск _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ _ 2022 г ньшен в порядке и случаях. 7. 3. Участник закупки, с которым заключается контракт по результатам определения Поставщика в соответствии с п. 1 ч. 1 ст. 30 Закона № 44 - ФЗ, освобождается от предоставления обеспечения исполнения контракта, в том числе с учетом ст. 37 Закона № 44 - ФЗ, от обеспечения гарантийных обязательств в случае предоставления таким участником закупки информации, содержащейся в реестре контрактов, заключенных заказчиками, и подтверждающей исполнение таким участником в течение трех лет до даты подачи заявки на участие в закупке трех контрактов, исполненных без применения к такому участнику неустоек ( штрафов, пеней ). Такая инфор

In [18]:
max_length = 512
stride = 128

def preprocess_training_examples(examples):
    inputs = tokenizer(
        examples["question"],
        examples["context"],
        max_length=max_length,
        truncation="only_second", 
        stride=stride,  
        return_overflowing_tokens=True,  
        return_offsets_mapping=True, 
        padding="max_length" 
    )

    offset_mapping = inputs.pop("offset_mapping")
    sample_map = inputs.pop("overflow_to_sample_mapping")
    answers = examples['answers']
    start_positions = []
    end_positions = []

    for i, offset in enumerate(offset_mapping):
        sample_idx = sample_map[i]
        answer = answers[sample_idx]
        start_char = answer["answer_start"]
        end_char = answer["answer_end"]

        sequence_ids = inputs.sequence_ids(i)

        #Поиск начала и конца контекста
        idx = 0
        while sequence_ids[idx] != 1:
            idx += 1
        context_start = idx
        while sequence_ids[idx] == 1:
            idx += 1
        context_end = idx - 1

        # Если ответ не в данном контексте, то (0, 0)
        if (start_char == 0 and end_char == 0) or offset[context_start][0] > start_char or offset[context_end][1] < end_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Если ответ в контексте, то начало и конец это токены
            idx = context_start
            while idx <= context_end and offset[idx][0] <= start_char:
                idx += 1
            start_positions.append(idx - 1)

            idx = context_end
            while idx >= context_start and offset[idx][1] >= end_char:
                idx -= 1
            end_positions.append(idx + 1)

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions

    return inputs

In [19]:
max_length = 512
stride = 128

def preprocess_validation_examples(examples):
    inputs = tokenizer(
        examples["question"],
        examples["context"],
        max_length=max_length,
        truncation="only_second", 
        stride=stride, 
        return_overflowing_tokens=True, 
        return_offsets_mapping=True, 
        padding="max_length" 
    )

    offset_mapping = inputs["offset_mapping"]
    sample_map = inputs.pop("overflow_to_sample_mapping")
    answers = examples['answers']
    start_positions = []
    end_positions = []
    example_ids = []

    for i, offset in enumerate(offset_mapping):
        sample_idx = sample_map[i]
        answer = answers[sample_idx]
        start_char = answer["answer_start"]
        end_char = answer["answer_end"]

        sequence_ids = inputs.sequence_ids(i)

        #Поиск начала и конца контекста
        idx = 0
        while sequence_ids[idx] != 1:
            idx += 1
        context_start = idx
        while sequence_ids[idx] == 1:
            idx += 1
        context_end = idx - 1

        # Если ответ не в данном контексте, то (0, 0)
        if (start_char == 0 and end_char == 0) or offset[context_start][0] > start_char or offset[context_end][1] < end_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Если ответ в контексте, то начало и конец это токены
            idx = context_start
            while idx <= context_end and offset[idx][0] <= start_char:
                idx += 1
            start_positions.append(idx - 1)

            idx = context_end
            while idx >= context_start and offset[idx][1] >= end_char:
                idx -= 1
            end_positions.append(idx + 1)

    for i in range(len(inputs["input_ids"])):
        sample_idx = sample_map[i]
        example_ids.append(examples["id"][sample_idx])

        sequence_ids = inputs.sequence_ids(i)
        offset = inputs["offset_mapping"][i]
        inputs["offset_mapping"][i] = [
            o if sequence_ids[k] == 1 else None for k, o in enumerate(offset)
        ]

    inputs["example_id"] = example_ids

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions

    return inputs

In [12]:
!pip install datasets evaluate transformers[sentencepiece]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.7/468.7 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 kB 11.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 15.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 kB 18.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 40.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 kB 21.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 29.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 21.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 19.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 269.3/269.3 kB 29.4 MB/s eta 0:00:00
  Attempting uni

In [14]:
import datasets
train_dataset2 = datasets.Dataset.from_pandas(train_data)
val_dataset2 = datasets.Dataset.from_pandas(val_data)

In [20]:
train_dataset = train_dataset2.map(
    preprocess_training_examples,
    batched=True,
    remove_columns=train_dataset2.column_names
)

Map:   0%|          | 0/1439 [00:00<?, ? examples/s]

In [21]:
train_dataset

Dataset({
    features: ['input_ids', 'token_type_ids', 'attention_mask', 'start_positions', 'end_positions'],
    num_rows: 1999
})

In [22]:
validation_dataset = val_dataset2.map(
    preprocess_validation_examples,
    batched=True,
    remove_columns=val_dataset2.column_names,
)

Map:   0%|          | 0/360 [00:00<?, ? examples/s]

In [23]:
validation_dataset

Dataset({
    features: ['input_ids', 'token_type_ids', 'attention_mask', 'offset_mapping', 'example_id', 'start_positions', 'end_positions'],
    num_rows: 566
})

In [24]:
import torch
from transformers import AutoModelForQuestionAnswering

Метрика для задачи "Questing-Answering"

In [25]:
import evaluate

metric = evaluate.load("squad")

Загрузка модели

In [26]:
model = AutoModelForQuestionAnswering.from_pretrained(model_checkpoint)

Some weights of the model checkpoint at cointegrated/rubert-tiny2 were not used when initializing BertForQuestionAnswering: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForQuestionAnswering were not initialized from the

In [27]:
from transformers import TrainingArguments

args = TrainingArguments(
    "rubert_tiny_qa_kontur",
    do_eval=True,
    evaluation_strategy="steps",
    eval_steps=500,
    logging_strategy="steps",
    save_strategy="steps",
    learning_rate=3e-5,#
    num_train_epochs=15,
    weight_decay=0.01,
    fp16=True,
    push_to_hub=True,
)
     

Авторизация Hugging face с помощью токена

In [28]:
from huggingface_hub import notebook_login

notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


Обучение

In [29]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    args=args,
    train_dataset=train_dataset,
    eval_dataset=validation_dataset,
    tokenizer=tokenizer,
)

Cloning https://huggingface.co/Stacy123/rubert_tiny_qa_kontur into local empty directory.


In [30]:
trainer.train()

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:391: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a BertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=3750, training_loss=0.5772412089029948, metrics={'train_runtime': 352.8405, 'train_samples_per_second': 84.982, 'train_steps_per_second': 10.628, 'total_flos': 212120119203840.0, 'train_loss': 0.5772412089029948, 'epoch': 15.0})

Расчет метрик

In [31]:
from tqdm.auto import tqdm
import collections

n_best = 20
max_answer_length = 30

def compute_metrics(start_logits, end_logits, features, examples):
    example_to_features = collections.defaultdict(list)
    for idx, feature in enumerate(features):
        example_to_features[feature["example_id"]].append(idx)

    predicted_answers = []
    for example in tqdm(examples):
        example_id = example["id"]
        context = example["context"]
        answers = []

        for feature_index in example_to_features[example_id]:
            start_logit = start_logits[feature_index]
            end_logit = end_logits[feature_index]
            offsets = features[feature_index]["offset_mapping"]

            start_indexes = np.argsort(start_logit)[-1 : -n_best - 1 : -1].tolist()
            end_indexes = np.argsort(end_logit)[-1 : -n_best - 1 : -1].tolist()
            for start_index in start_indexes:
                for end_index in end_indexes:
                    if offsets[start_index] is None or offsets[end_index] is None:
                        continue
                    if (
                        end_index < start_index
                        or end_index - start_index + 1 > max_answer_length
                    ):
                        continue

                    answer = {
                        "text": context[offsets[start_index][0] : offsets[end_index][1]],
                        "logit_score": start_logit[start_index] + end_logit[end_index],
                    }
                    answers.append(answer)

        if len(answers) > 0:
            best_answer = max(answers, key=lambda x: x["logit_score"])
            predicted_answers.append(
                {"id": str(example_id), "prediction_text": best_answer["text"]}
            )
        else:
            predicted_answers.append({"id": str(example_id), "prediction_text": ""})
    theoretical_answers = [{'id': str(ex["id"]), 'answers': {'text': [ex["answers"]["text"]], 'answer_start': [ex["answers"]["answer_start"]]}} for ex in examples]
    return metric.compute(predictions=predicted_answers, references=theoretical_answers)

In [32]:
import numpy as np

In [33]:
predictions, _, _ = trainer.predict(validation_dataset)
start_logits, end_logits = predictions
compute_metrics(start_logits, end_logits, validation_dataset, val_dataset2)

  0%|          | 0/360 [00:00<?, ?it/s]

{'exact_match': 82.77777777777777, 'f1': 94.30348903895964}